In [1]:
import pandas as pd
import numpy as np
import os, sys, copy, argparse
import json
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor(config_name='revised')

In [3]:
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-5. 테이블을 표준화했습니다.
1-6. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [4]:
self.make_matching()

In [5]:
# 모든 inter_no(교차로번호)에 대한 A, B링 현시별 이동류정보
self.match1.head()

inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2

In [6]:
# match1을 계층화한 테이블
self.match2.head()

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6

In [7]:
# match2의 각 이동류번호에 진입방향, 진출방향을 매칭시킨 테이블
self.match3.head()

inter_no  phase_no ring_type  move_no inc_dire out_dire
0       175         1         A        8        남        북
1       175         1         B        4        북        남
2       175         2         A        7        북        동
3       175         2         B        3        남        서
4       175         3         A        6        동        서

In [8]:
# match3의 각 이동류번호에 진입/진출 방위각을 매칭시킨 테이블
self.match4.head()

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle out_angle
0       175         1         A        8        남        북       179       004
1       175         1         B        4        북        남       003       176
2       175         2         A        7        북        동       001       095
3       175         2         B        3        남        서       179       271
4       175         3         A        6        동        서       092       270

In [9]:
# match4의 각 행에 진입엣지id, 진출엣지id 노드id 추가한 테이블
self.match5.head()

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       003   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       092   

  out_angle    inc_edge_id   out_edge_id node_id node_type turn_type  
0       004  -571542797_02  571500487_01      i0    normal  straight  
1       176  -571500487_01  571542797_02      i0    normal  straight  
2       095  -571500487_01  571545870_01      i0    normal      left  
3       271  -571542797_02  571510153_01      i0    normal      left  
4       270   571545870_02  571510153_01      i0    normal  straight

In [10]:
# match5에서 부교차로(유턴교차로, 연동교차로)에 대한 행들을 추가함
self.match6.head()

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       003   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       092   

  out_angle    inc_edge_id   out_edge_id node_id node_type turn_type  
0       004  -571542797_02  571500487_01      i0    normal  straight  
1       176  -571500487_01  571542797_02      i0    normal  straight  
2       095  -571500487_01  571545870_01      i0    normal      left  
3       271  -571542797_02  571510153_01      i0    normal      left  
4       270   571545870_02  571510153_01      i0    normal  straight

In [11]:
# 각 교차로에 대하여, 가능한 모든 이동류 (1~16)에 대한 진입·진출엣지ID를 지정한 테이블
self.matching.head()

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
0       175      i0        1        동        남   571545870_02  571542797_02   
1       175      i0        2        서        동   571510153_02  571545870_01   
2       175      i0        3        남        서  -571542797_02  571510153_01   
3       175      i0        4        북        남  -571500487_01  571542797_02   
4       175      i0        5        서        북   571510153_02  571500487_01   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left

In [12]:
self.initialize_state()
self.assign_indices()
self.assign_signals()

2-2. 초기화 신호가 지정되었습니다. (우회전 : g)
2-3. 유턴 인덱스 / 비보호좌회전 인덱스를 지정했습니다.
2-4. 직진 및 좌회전(G)을 배정했습니다.


In [14]:
# 신호배정
self.match6.head()

inter_no node_id  phase_no ring_type  move_no    inc_edge_id   out_edge_id  \
0       175      i0         1         A        8  -571542797_02  571500487_01   
1       175      i0         1         B        4  -571500487_01  571542797_02   
2       175      i0         2         A        7  -571500487_01  571545870_01   
3       175      i0         2         B        3  -571542797_02  571510153_01   
4       175      i0         3         A        6   571545870_02  571510153_01   

               state turn_type  
0  grrrgrrrgGGGGrgrr  straight  
1  gGGrgrrrgrrrrrgrr  straight  
2  grrGgrrrgrrrrrgrr      left  
3  grrrgrrrgrrrrGgrr      left  
4  grrrgGGrgrrrrrgrr  straight

In [15]:
# 신호배정
self.matching.head()

inter_no node_id  move_no    inc_edge_id   out_edge_id              state  \
0       175      i0        1   571545870_02  571542797_02  grrrgrrGgrrrrrgrr   
1       175      i0        2   571510153_02  571545870_01  grrrgrrrgrrrrrgGr   
2       175      i0        3  -571542797_02  571510153_01  grrrgrrrgrrrrGgrr   
3       175      i0        4  -571500487_01  571542797_02  gGGrgrrrgrrrrrgrr   
4       175      i0        5   571510153_02  571500487_01  grrrgrrrgrrrrrgrG   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left